# Setting up conection 

In [20]:
from sqlalchemy import create_engine, MetaData, Table
from sqlalchemy.orm import mapper, sessionmaker
from sqlalchemy import Column, Integer
from sqlalchemy.ext.declarative import declarative_base
from scrapy.selector import Selector
from sqlalchemy.sql import text as sa_text
import re

engine = create_engine('mysql+pymysql://root:@localhost/oersdb', echo=False)
Base = declarative_base(engine)

class Crawl(Base):
    __tablename__ = 'crawl'
    __table_args__ = {'autoload': True}


class Triplete(Base):
    __tablename__ = 'triplete'
    __table_args__ = {'autoload': True}

metadata = Base.metadata
Session = sessionmaker(bind=engine)
session = Session()

print("Done, ready DB")

Done, ready DB


In [21]:
triples = session.query(Crawl).filter(Crawl.subject =="oasis")
print(triples)
print("Cleaned")

SELECT crawl.id AS crawl_id, crawl.subject AS crawl_subject, crawl.predicate AS crawl_predicate, crawl.object AS crawl_object, crawl.source AS crawl_source 
FROM crawl 
WHERE crawl.subject = %(subject_1)s
Cleaned


In [22]:
source_raw = "OAsis"
for triple in triples:
    body = triple.object
    source = triple.source
    # Setting name
    name = Selector(text=body).xpath("//h2/text()").get()  
    name_triple =  name.replace(" ", "_")
    name_triple =  name_triple.replace("/", "")
    name_triple =  name_triple.replace(":", "")
    print('_ _ _ _')
    print('name')
    print('_ _ _ _')
    print(name_triple)
    #session.add(CleanTriple(subject_uri=source ,subject_id =source_raw, predicate='Name', object=name_triple))
    
    table_predicate = Selector(text=body).xpath("//td[@class='label-cell']/text()").getall()
    table_object = Selector(text=body).xpath("//td[@class='word-break']/text()").getall()
    if table_object is not None and table_predicate is not None:
        for predicate, object in zip(table_predicate, table_object):
            print(predicate, ' : ', object)
            p = predicate.split('.')
            del p[0]
            pred = ''
            j = 0
            for i in p:
                if j > 0:
                    i = i.capitalize()
                pred = pred + i
                j = j+1
            session.add(Triplete(subject = name_triple, repository = source_raw, predicate = pred, object = object))
    
    files = Selector(text=body).xpath('//div[@class="file-wrapper row"]').getall()
    j=1
    obj_files = []
    if files is not None:
        session.add(Triplete(subject = name_triple, repository = source_raw, predicate = 'numberOfFiles', object = len(files)))
        for f in files:
            obj = ':File_' + str(j) + '_of_' + name_triple
            obj_files.append(obj)
            j+=1
            print('file : ', obj)
            session.add(Triplete(subject = name_triple, repository = source_raw, predicate = 'hasFile', object = obj))
            
        for file, o in zip(files, obj_files):
            img = Selector(text=file).xpath('//div[@class="file-wrapper row"]/div/div/a/img/@src').getall()
            fl = Selector(text=file).xpath('//a/@href').getall()
            img = ["%s%s" % ('http://oasis.col.org', s) for s in img]
            fl = ["%s%s" % ('http://oasis.col.org', s) for s in fl]
            
            files_predicate = Selector(text=file).xpath('//dl[@class="file-metadata dl-horizontal"]/dt/text()').getall()
            files_object = Selector(text=file).xpath('//dl[@class="file-metadata dl-horizontal"]/dd/text()').getall()
            if files_object is not None and files_predicate is not None:
                for predicate, object in zip(files_predicate, files_object):
                    print(predicate, ' : ', object)
                    predicate = 'file' + predicate
                    predicate = predicate.replace(':', '')
                    o = o.replace(':', '')
                    session.add(Triplete(subject=o, repository = source_raw, predicate = predicate, object = object))
            print('img :', img[0])
            print('file : ', fl[0])
            session.add(Triplete(subject = o, repository = source_raw, predicate = 'fileImage', object = img[0]))
            session.add(Triplete(subject = o, repository = source_raw, predicate = 'fileUrl', object = fl[0]))
            
print("Done")     
session.commit()
session.close_all()

_ _ _ _
name
_ _ _ _
Advancing_Research_in_Commonwealth_Africa_Some_Reflections
dc.contributor.author  :  Kanwar, Asha
dc.contributor.author  :  Gatsha, Godson
dc.contributor.author  :  Lesperance, John
dc.contributor.author  :  Mishra, Sanjaya
dc.date.accessioned  :  2015-04-22T17:41:42Z
dc.date.available  :  2015-04-22T17:41:42Z
dc.date.issued  :  2015-02-12
dc.identifier.uri  :  http://hdl.handle.net/11599/770
dc.description.abstract  :  Transcript and presentation slides of a speech given  at the Commonwealth Tertiary Education Facility (CTEF), Malaysia, 12 February 2015. Presented by Professor Asha Kanwar, President & CEO (co-written with Dr. Godson Gatsha, Mr. John Lesperance, and Dr. Sanjaya Mishra)
dc.language.iso  :  en
dc.publisher  :  Commonwealth of Learning, Vancouver
dc.subject  :  Research
dc.title  :  Advancing Research in Commonwealth Africa: Some Reflections
dc.type  :  Presentation
col.region  :  Africa
file :  :File_1_of_Advancing_Research_in_Commonwealth_Africa_Som

/home/odmendoza/Repositories/oers_scrapy/venv/lib/python3.6/site-packages/ipykernel_launcher.py:66: SADeprecationWarning: The Session.close_all() method is deprecated and will be removed in a future release.  Please refer to session.close_all_sessions().
